In [1]:
import pandas as pd
import csv
import numpy as np

### Train

In [2]:
bm25_all_file_path_train = 'results/train/subtask_2a_bm25_english_all_qrels-train.tsv'
bm25_vclaim_file_path_train = 'results/train/subtask_2a_bm25_english_vclaim_qrels-train.tsv'
bm25_title_file_path_train = 'results/train/subtask_2a_bm25_english_title_qrels-train.tsv'
sbert_file_path_train = 'results/train/subtask_2a_sbert_english_qrels-train.tsv'
train_file_path = 'Project/Fact-checked-Claim-Detection/data/subtask-2a--english/qrels-train.tsv'

In [3]:
N = 50
cnt_vclaims = 13824
cnt_iclaims = 997

In [4]:
bm25_all_train_results = pd.read_csv(bm25_all_file_path_train, sep = '\t', names = ['iclaim_id', 'Q0', 'vclaim_id', 'rank', 'score', 'method'])
bm25_vclaim_train_results = pd.read_csv(bm25_vclaim_file_path_train, sep = '\t', names = ['iclaim_id', 'Q0', 'vclaim_id', 'rank', 'score', 'method'])
bm25_title_train_results = pd.read_csv(bm25_title_file_path_train, sep = '\t', names = ['iclaim_id', 'Q0', 'vclaim_id', 'rank', 'score', 'method'])
sbert_train_results = pd.read_csv(sbert_file_path_train, sep = '\t', names =['iclaim_id', 'Q0', 'vclaim_id', 'rank', 'score', 'method'])

In [5]:
train_results = pd.read_csv(train_file_path, sep = '\t', names = ['iclaim_id', 'Q0', 'vclaim_id', 'relevance'])

In [6]:
bm25_all_train_results.head()

iclaim_id  Q0                                 vclaim_id  rank      score  \
0  tweet-sno-0  Q0   vclaim-sno-hero-wombats-australia-fires     1  21.490473   
1  tweet-sno-0  Q0         vclaim-sno-lincoln-tunnel-flooded     2  16.735357   
2  tweet-sno-0  Q0      vclaim-sno-australia-fires-iss-image     3  14.600450   
3  tweet-sno-0  Q0  vclaim-sno-static-electricity-pump-fires     4  13.367122   
4  tweet-sno-0  Q0      vclaim-sno-how-green-was-my-ballyhoo     5  13.106119   

   method  
0  elasic  
1  elasic  
2  elasic  
3  elasic  
4  elasic

In [7]:
bm25_vclaim_train_results.head()

iclaim_id  Q0                                          vclaim_id  rank  \
0  tweet-sno-0  Q0                vclaim-sno-zebra-lion-watering-hole     1   
1  tweet-sno-0  Q0                  vclaim-sno-bitterroot-forest-fire     2   
2  tweet-sno-0  Q0                      vclaim-sno-fox-feeding-koalas     3   
3  tweet-sno-0  Q0  vclaim-sno-forestry-service-advice-for-animals...     4   
4  tweet-sno-0  Q0  vclaim-sno-is-this-video-of-an-airplane-on-fir...     5   

       score  method  
0  14.891502  elasic  
1  13.392576  elasic  
2  13.333019  elasic  
3  11.752324  elasic  
4  11.650006  elasic

In [8]:
bm25_title_train_results.head()

iclaim_id  Q0                                vclaim_id  rank      score  \
0  tweet-sno-0  Q0  vclaim-sno-hero-wombats-australia-fires     1  16.111873   
1  tweet-sno-0  Q0     vclaim-sno-australia-fires-iss-image     2  12.297370   
2  tweet-sno-0  Q0        vclaim-sno-microwave-water-plants     3  12.276060   
3  tweet-sno-0  Q0         vclaim-sno-obituary-common-sense     4   9.688478   
4  tweet-sno-0  Q0     vclaim-sno-why-wombat-poop-is-square     5   9.510785   

   method  
0  elasic  
1  elasic  
2  elasic  
3  elasic  
4  elasic

In [9]:
sbert_train_results.head()

iclaim_id  Q0                                          vclaim_id  rank  \
0  tweet-sno-0  Q0                      vclaim-sno-bees-gmo-cornfield     1   
1  tweet-sno-0  Q0            vclaim-sno-hero-wombats-australia-fires     2   
2  tweet-sno-0  Q0                        vclaim-sno-fawn-bobcat-fire     3   
3  tweet-sno-0  Q0  vclaim-sno-did-sprinklers-save-house-from-mass...     4   
4  tweet-sno-0  Q0                       vclaim-sno-rainbow-butterfly     5   

      score method  
0  0.463434  sbert  
1  0.435456  sbert  
2  0.432011  sbert  
3  0.427477  sbert  
4  0.415195  sbert

In [10]:
train_results.head()

iclaim_id  Q0                                   vclaim_id  relevance
0  tweet-sno-0   0     vclaim-sno-hero-wombats-australia-fires          1
1  tweet-sno-1   0   vclaim-sno-ilhan-omar-treason-advice-iran          1
2  tweet-sno-2   0   vclaim-sno-us-army-sending-texts-on-draft          1
3  tweet-sno-3   0   vclaim-sno-us-army-sending-texts-on-draft          1
4  tweet-sno-4   0  vclaim-sno-video-of-drone-strike-soleimani          1

In [11]:
def get_rr_score(results, iclaim, vclaim, index):
    curr_index = index
    while curr_index < len(results):
        if(iclaim == results.loc[curr_index, 'iclaim_id'] and vclaim == results.loc[curr_index, 'vclaim_id']):
            return (results.loc[curr_index, 'score'], 1/ results.loc[curr_index,'rank'])
        curr_index = curr_index + 1

In [12]:
def get_vclaims(results, iclaim):
    vclaims = []
    for index in range(len(results)):
        if results.loc[index, 'iclaim_id'] == iclaim:
            vclaims.append(results.loc[index,'vclaim_id'])
    
    return vclaims

In [13]:
print(len(bm25_all_train_results))

13782528


In [14]:
i = 0
qid = 1
index = 0
start_index = 0
rank_svm_info = []
main_results = sbert_train_results
while index < len(main_results):
    
    iclaim_id = main_results.loc[index, 'iclaim_id']
    
    if i < N:
        i = i + 1
        bm25_title_features = get_rr_score(bm25_title_train_results, 
                                           main_results.loc[index, 'iclaim_id'], 
                                           main_results.loc[index, 'vclaim_id'], 
                                           start_index)
        
        bm25_vclaim_features = get_rr_score(bm25_vclaim_train_results, 
                                            main_results.loc[index, 'iclaim_id'], 
                                            main_results.loc[index, 'vclaim_id'], 
                                            start_index)
        
#         sbert_features = get_rr_score(sbert_train_results, 
#                                       main_results.loc[index, 'iclaim_id'], 
#                                       main_results.loc[index, 'vclaim_id'], 
#                                       start_index)
        
        bm25_all_features = get_rr_score(bm25_all_train_results, 
                                      main_results.loc[index, 'iclaim_id'], 
                                      main_results.loc[index, 'vclaim_id'], 
                                      start_index)
        target = 2
        if main_results.loc[index, 'vclaim_id'] in get_vclaims(train_results, main_results.loc[index, 'iclaim_id']):
            target = 1
        
#         rank_svm_info.append(str(target) + ' qid:' + str(qid) 
#                              + ' 1:' + str(main_results.loc[index, 'score'])
#                              + ' 2:' + str(1/main_results.loc[index, 'rank'])
#                              + ' 3:' + str(bm25_title_features[0]) 
#                              + ' 4:' + str(bm25_title_features[1]) 
#                              + ' 5:' + str(bm25_vclaim_features[0]) 
#                              + ' 6:' + str(bm25_vclaim_features[1]) 
#                              + ' 7:' + str(sbert_features[0]) 
#                              + ' 8:' + str(sbert_features[1]) 
#                             )

        rank_svm_info.append(str(target) + ' qid:' + str(qid) 
                         + ' 1:' + str(main_results.loc[index, 'score'])
                         + ' 2:' + str(1/main_results.loc[index, 'rank'])
                         + ' 3:' + str(bm25_title_features[0]) 
                         + ' 4:' + str(bm25_title_features[1]) 
                         + ' 5:' + str(bm25_vclaim_features[0]) 
                         + ' 6:' + str(bm25_vclaim_features[1]) 
                         + ' 7:' + str(bm25_all_features[0]) 
                         + ' 8:' + str(bm25_all_features[1]) 
                        )
        index = index + 1

    else:
        print(qid)
        qid = qid + 1
        i = 0

        while index < len(main_results) and main_results.loc[index, 'iclaim_id'] == iclaim_id:
            index = index + 1
        
        start_index = index


1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
277


In [ ]:
print(rank_svm_info)

In [15]:
with open('rank_top' + str(N) + '_train_sbert', 'w') as f:
    for item in rank_svm_info:
        f.write("%s\n" % item)

#### Test for train

In [32]:
#TRAIN RANK SVM
#svm_rank_learn -c 38 subtask2a/rank_top20 subtask2a/model_top20_linear
#test: svm_rank_classify subtask2a/rank_top20 subtask2a/model_top20_linear subtask2a/predictions_top20_linear

N = 50
cnt_iclaims = 997
#load rank svm results
#rank_svm_results = open("predictions", "r")
#rank_svm_results = open('predictions_top' + str(N) + '_rbf', "r")
#rank_svm_results = open('predictions_top10_train_c1_sbert (1)', 'r')
rank_svm_results = open('predictions_top50_train.txt', 'r')

predictions = rank_svm_results.read().split('\n')
print(predictions)
close(rank_svm_results)

['-1.51406551', '-4.85762705', '-1.54838950', '-1.58903075', '-0.40566243', '-1.52413478', '-0.32406993', '-0.29925049', '-0.27843438', '-1.24101818', '-0.24717720', '-0.23655200', '-0.22756722', '-0.21895947', '-0.88418909', '-1.78275761', '-0.20052285', '-0.19598342', '-2.58261256', '-0.18679150', '-0.18282678', '-1.51077383', '-1.91192495', '-0.17331607', '-0.17101885', '-0.16842972', '-0.91976254', '-1.10895062', '-2.61130626', '-0.16035069', '-1.69226157', '-0.15728392', '-0.15598525', '-0.15442304', '-1.29040427', '-0.15099182', '-0.14958489', '-1.30757186', '-0.92598723', '-0.14582870', '-0.14474528', '-0.14383051', '-1.12717081', '-0.14153941', '-0.14070602', '-0.13996105', '-0.54910020', '-0.76533154', '-0.74499633', '-0.13715503', '-6.66311224', '-2.06497952', '-2.03499515', '-0.93073743', '-2.62118636', '-2.09725229', '-0.72014711', '-0.29799669', '-1.18878431', '-1.09141364', '-0.24644214', '-0.23543230', '-0.22564019', '-0.52092259', '-0.93883742', '-0.56351663', '-1.53933

NameError: name 'close' is not defined

In [33]:
predictions = np.array(predictions[:-1]).reshape(cnt_iclaims, N)

In [34]:
print(predictions)

[['-1.51406551' '-4.85762705' '-1.54838950' ... '-0.76533154'
  '-0.74499633' '-0.13715503']
 ['-6.66311224' '-2.06497952' '-2.03499515' ... '-0.57886023'
  '-0.13754540' '-0.13685728']
 ['-8.13218142' '-4.02931395' '-1.65087116' ... '-2.68222049'
  '-0.14779198' '-1.19978842']
 ...
 ['-6.82559687' '-3.59464078' '-2.47733789' ... '-2.75494741'
  '-1.51004282' '-2.65412281']
 ['-6.27677706' '-0.81454973' '-0.98683679' ... '-0.12882146'
  '-0.97354542' '-0.12661046']
 ['-9.49719527' '-3.15230151' '-0.98071812' ... '-0.64347979'
  '-0.82854276' '-0.10722823']]


In [35]:
iclaim_index = 0
index = 0
all_scores = {}
main_results = sbert_train_results
while index < len(main_results):
    
    iclaim_id = main_results.loc[index, 'iclaim_id']
    scores = {}
    i = 0
    
    while i < N:
        scores[main_results.loc[index, 'vclaim_id']] = -float(predictions[iclaim_index][i]) 
        # ranksvm scores sort queries in ascending order
        # evaluation requires the first queries to have the highes score
        i = i + 1
        index = index + 1
        
    #while i < iclaims_cnt:
   #     scores[bm25_vclaim_results.loc[index, 'vclaim_id']] = bm25_vclaim_results.loc[index, 'score']
   #     i = i + 1
    #    index = index + 1
    
    print(scores)
    scores = sorted(list(scores.items()), key=lambda kv: kv[1], reverse=True)
    print(iclaim_id, scores)
    all_scores[iclaim_id] = scores
    iclaim_index = iclaim_index + 1
    index = index - N + cnt_vclaims

{'vclaim-sno-bees-gmo-cornfield': 1.51406551, 'vclaim-sno-hero-wombats-australia-fires': 4.85762705, 'vclaim-sno-fawn-bobcat-fire': 1.5483895, 'vclaim-sno-did-sprinklers-save-house-from-massive-wildfire': 1.58903075, 'vclaim-sno-rainbow-butterfly': 0.40566243, 'vclaim-sno-floating-islands-of-fire-ants': 1.52413478, 'vclaim-sno-zoo-animals-escape-floyd-protests': 0.32406993, 'vclaim-sno-bumblebees-cant-fly': 0.29925049, 'vclaim-sno-rain-wildfire-toxic': 0.27843438, 'vclaim-sno-frozen-frogs': 1.24101818, 'vclaim-sno-cthulhu-rising': 0.2471772, 'vclaim-sno-daisy-dog-rescued-911-survivors': 0.236552, 'vclaim-sno-striped-mittenfish': 0.22756722, 'vclaim-sno-whale-of-a-tale': 0.21895947, 'vclaim-sno-snakes-pool-noodles': 0.88418909, 'vclaim-sno-koala-australian-bushfires': 1.78275761, 'vclaim-sno-endangered-starry-butterfly-pix': 0.20052285, 'vclaim-sno-kitten-dies-due-home-depot-christmas-tree': 0.19598342, 'vclaim-sno-forestry-service-advice-for-animals-in-wildfires': 2.58261256, 'vclaim-s

tweet-sno-193 [('vclaim-sno-wall-street-border-wall', 5.86854233), ('vclaim-sno-andrew-yang-old-york', 2.50177021), ('vclaim-sno-el-paso-border-barrier-crime', 2.03339729), ('vclaim-sno-sea-foam-fill-streets-in-spain', 2.01980481), ('vclaim-sno-breach-capitol-british-1814', 1.66565315), ('vclaim-sno-stocking-the-true-origin', 1.60718408), ('vclaim-sno-no-way-no-jay', 1.57468866), ('vclaim-sno-houses-in-unusual-places', 1.56925776), ('vclaim-sno-aoc-wall-mountains', 1.55009058), ('vclaim-sno-politicians-walls-around-homes', 1.4126667), ('vclaim-sno-covid-detention-camps-new-york', 1.30943032), ('vclaim-sno-san-antonio-border-wall', 1.19103399), ('vclaim-sno-crips', 1.18786806), ('vclaim-sno-uss-new-york', 1.17689438), ('vclaim-sno-elephant-seal-chilean-town', 1.14134638), ('vclaim-sno-ronald-reagan-border-wall-idea', 1.1044032), ('vclaim-sno-new-york-easter-cross-light-display', 1.0440591), ('vclaim-sno-ventilators-warehouse-new-york', 1.02199643), ('vclaim-sno-nyc-premarked-ballots', 1

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [36]:
print(all_scores)

{'tweet-sno-0': [('vclaim-sno-hero-wombats-australia-fires', 4.85762705), ('vclaim-sno-australia-fires-iss-image', 2.61130626), ('vclaim-sno-forestry-service-advice-for-animals-in-wildfires', 2.58261256), ('vclaim-sno-clouds-over-australian-bushfires', 1.91192495), ('vclaim-sno-koala-australian-bushfires', 1.78275761), ('vclaim-sno-coral-reef-empire-state-building', 1.69226157), ('vclaim-sno-did-sprinklers-save-house-from-massive-wildfire', 1.58903075), ('vclaim-sno-fawn-bobcat-fire', 1.5483895), ('vclaim-sno-floating-islands-of-fire-ants', 1.52413478), ('vclaim-sno-bees-gmo-cornfield', 1.51406551), ('vclaim-sno-jerry-brown-veto-wildfire-bill', 1.51077383), ('vclaim-sno-australia-cats', 1.30757186), ('vclaim-sno-wildfires-stop-borders', 1.29040427), ('vclaim-sno-frozen-frogs', 1.24101818), ('vclaim-sno-colorado-squirrel-bubonic-plague', 1.12717081), ('vclaim-sno-fire-and-rain', 1.10895062), ('vclaim-sno-guy-fieri-wildfires', 0.92598723), ('vclaim-sno-ted-cruz-texas-freezes-over', 0.919

In [37]:
def format_scores(scores):
    output_string = ''
    i = 1
    for iclaim_id in scores:
        i = i + 1
        for i, (vclaim_id, score) in enumerate(scores[iclaim_id]):
            output_string += f"{iclaim_id}\tQ0\t{vclaim_id}\t{i + 1}\t{score}\trank_svm\n"
    return output_string

In [38]:
formatted_scores = format_scores(all_scores)
rank_svm_file = 'rank_top' + str(N) + '_train_linear_sbert.tsv'
with open(rank_svm_file, 'w') as f:
    f.write(formatted_scores)

In [39]:
from scorer.main import evaluate
import logging

maps, mrr, precisions = evaluate(train_file_path, rank_svm_file)
logging.info(f'All MAP scores on threshold from [1, 3, 5, 10, 20, 50, 1000]. {maps}')
logging.info(f'MRR score {mrr}')
logging.info(f'All P scores on threshold from [1, 3, 5, 10, 20, 50, 1000]. {precisions}')

INFO : All MAP scores on threshold from [1, 3, 5, 10, 20, 50, 1000]. [0.7783350050150452, 0.8196255432965563, 0.8244399866265463, 0.8281304230150769, 0.8290477134911755, 0.8292273052026207, 0.8292273052026207]
INFO : MRR score 0.8292273052026207
INFO : All P scores on threshold from [1, 3, 5, 10, 20, 50, 1000]. [0.7793380140421263, 0.28986960882647944, 0.17813440320962892, 0.09157472417251757, 0.04643931795386159, 0.01867602808425276, 0.0009338014042126381]


### DEV

In [16]:
bm25_all_file_path_dev = 'results/dev/subtask_2a_bm25_english_all_qrels-dev.tsv'
bm25_vclaim_file_path_dev = 'results/dev/subtask_2a_bm25_english_vclaim_qrels-dev.tsv'
bm25_title_file_path_dev = 'results/dev/subtask_2a_bm25_english_title_qrels-dev.tsv'
sbert_file_path_dev = 'results/dev/subtask_2a_sbert_english_qrels-dev.tsv'
dev_file_path = 'Project/Fact-checked-Claim-Detection/data/subtask-2a--english/qrels-dev.tsv'

In [17]:
bm25_all_dev_results = pd.read_csv(bm25_all_file_path_dev, sep = '\t', names = ['iclaim_id', 'Q0', 'vclaim_id', 'rank', 'score', 'method'])
bm25_vclaim_dev_results = pd.read_csv(bm25_vclaim_file_path_dev, sep = '\t', names = ['iclaim_id', 'Q0', 'vclaim_id', 'rank', 'score', 'method'])
bm25_title_dev_results = pd.read_csv(bm25_title_file_path_dev, sep = '\t', names = ['iclaim_id', 'Q0', 'vclaim_id', 'rank', 'score', 'method'])
sbert_dev_results = pd.read_csv(sbert_file_path_dev, sep = '\t', names =['iclaim_id', 'Q0', 'vclaim_id', 'rank', 'score', 'method'])

In [18]:
dev_results = pd.read_csv(dev_file_path, sep = '\t', names = ['iclaim_id', 'Q0', 'vclaim_id', 'relevance'])

In [19]:
cnt_vclaims = 13824
cnt_iclaims = 199
N = 50

In [20]:
i = 0
qid = 1
index = 0
start_index = 0
rank_svm_info = []
main_results = sbert_dev_results
while index < len(main_results):
    if i < N:
        i = i + 1
        bm25_title_features = get_rr_score(bm25_title_dev_results, 
                                           main_results.loc[index, 'iclaim_id'], 
                                           main_results.loc[index, 'vclaim_id'], 
                                           start_index)
        
        bm25_vclaim_features = get_rr_score(bm25_vclaim_dev_results, 
                                            main_results.loc[index, 'iclaim_id'], 
                                            main_results.loc[index, 'vclaim_id'], 
                                            start_index)
        
#         sbert_features = get_rr_score(sbert_dev_results, 
#                                       main_results.loc[index, 'iclaim_id'], 
#                                       main_results.loc[index, 'vclaim_id'], 
#                                       start_index)
        
        bm25_all_features = get_rr_score(bm25_all_dev_results, 
                                      main_results.loc[index, 'iclaim_id'], 
                                      main_results.loc[index, 'vclaim_id'], 
                                      start_index)
        target = 2
        if main_results.loc[index, 'vclaim_id'] in get_vclaims(dev_results, main_results.loc[index, 'iclaim_id']):
            target = 1
        
#         rank_svm_info.append(str(target) + ' qid:' + str(qid) 
#                              + ' 1:' + str(main_results.loc[index, 'score'])
#                              + ' 2:' + str(1/main_results.loc[index, 'rank'])
#                              + ' 3:' + str(bm25_title_features[0]) 
#                              + ' 4:' + str(bm25_title_features[1]) 
#                              + ' 5:' + str(bm25_vclaim_features[0]) 
#                              + ' 6:' + str(bm25_vclaim_features[1]) 
#                              + ' 7:' + str(sbert_features[0]) 
#                              + ' 8:' + str(sbert_features[1]) 
#                             )

        rank_svm_info.append(str(target) + ' qid:' + str(qid) 
                         + ' 1:' + str(main_results.loc[index, 'score'])
                         + ' 2:' + str(1/main_results.loc[index, 'rank'])
                         + ' 3:' + str(bm25_title_features[0]) 
                         + ' 4:' + str(bm25_title_features[1]) 
                         + ' 5:' + str(bm25_vclaim_features[0]) 
                         + ' 6:' + str(bm25_vclaim_features[1]) 
                         + ' 7:' + str(bm25_all_features[0]) 
                         + ' 8:' + str(bm25_all_features[1]) 
                        )
        index = index + 1

    else:
        print(qid)
        qid = qid + 1
        i = 0
        index = index - N + cnt_vclaims
        start_index = index


1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199


In [420]:
print(rank_svm_info)

['1 qid:1 1:0.5752015113830566 2:1.0 3:27.012237950334768 4:1.0 5:23.815852486313585 6:1.0 7:24.39000186062631 8:1.0', '2 qid:1 1:0.4742061495780945 2:0.5 3:0.0 4:8.487523340689187e-05 5:0.0 6:8.444519506840061e-05 7:3.070615206870637 8:0.0004655493482309125', '2 qid:1 1:0.4718949198722839 2:0.3333333333333333 3:5.377512162651888 4:0.005649717514124294 5:6.406762802444757 6:0.012987012987012988 7:6.617701605549858 8:0.0033222591362126247', '2 qid:1 1:0.4643775224685669 2:0.25 3:5.055356161241956 4:0.0044444444444444444 5:5.613949921363765 6:0.006024096385542169 7:8.288405124874387 8:0.012345679012345678', '2 qid:1 1:0.4451855421066284 2:0.2 3:0.0 4:0.0006618133686300463 5:0.0 6:0.0005422993492407809 7:0.0 8:0.00020508613617719443', '2 qid:1 1:0.4403455555438995 2:0.16666666666666666 3:7.217194671828056 4:0.03225806451612903 5:4.094071803969363 6:0.001366120218579235 7:5.803498705788056 8:0.0018248175182481751', '2 qid:1 1:0.434619128704071 2:0.14285714285714285 3:0.0 4:0.00046576618537

In [21]:
with open('rank_top' + str(N) + '_dev_sbert', 'w') as f:
    for item in rank_svm_info:
        f.write("%s\n" % item)

In [ ]:
#Classify on RankSVM

In [24]:
N = 50
cnt_iclaims = 199
#load rank svm results
#rank_svm_results = open("predictions", "r")
#rank_svm_results = open('predictions_top' + str(N) + '_rbf', "r")
#rank_svm_results = open('predictions_top20_dev_linear_sbert', "r")
rank_svm_results = open('predictions_top50_dev', "r")

predictions = rank_svm_results.read().split('\n')
print(predictions)
close(rank_svm_results)

['-6.97253121', '-1.31640143', '-2.03723564', '-2.13819059', '-0.41527229', '-1.57914851', '-0.75786876', '-3.45746749', '-0.28834882', '-0.27291413', '-1.68341976', '-0.24459463', '-0.61402807', '-0.65027818', '-1.83833074', '-0.77786594', '-1.42127178', '-0.20294921', '-1.36571096', '-0.19481901', '-1.08683109', '-0.18844199', '-1.79273443', '-0.18191962', '-1.53119299', '-1.92247365', '-0.50734680', '-1.39521772', '-0.97078307', '-1.44217144', '-0.16582747', '-0.16438324', '-0.76035402', '-1.50218553', '-0.15994226', '-1.03585755', '-1.16426224', '-0.74480631', '-0.52243610', '-1.33788313', '-1.98781487', '-0.15257741', '-1.35663968', '-0.57493572', '-0.57377603', '-1.47773517', '-0.14830855', '-0.78525036', '-1.12397227', '-1.55444116', '-8.18642350', '-2.18498839', '-1.93394581', '-1.57330511', '-1.62437358', '-1.53392999', '-0.33400352', '-1.66843976', '-0.89660764', '-0.27313446', '-0.76289140', '-2.08449646', '-1.53128873', '-0.23094291', '-0.97910745', '-0.21711607', '-0.80773

NameError: name 'close' is not defined

In [25]:
predictions = np.array(predictions[:-1]).reshape(cnt_iclaims, N)

In [26]:
main_results = sbert_dev_results

In [27]:
iclaim_index = 0
index = 0
all_scores = {}
while index < len(main_results):
    
    iclaim_id = main_results.loc[index, 'iclaim_id']
    scores = {}
    i = 0
    
    while i < N:
        scores[main_results.loc[index, 'vclaim_id']] = -float(predictions[iclaim_index][i]) 
        # ranksvm scores sort queries in ascending order
        # evaluation requires the first queries to have the highes score
        i = i + 1
        index = index + 1
        
    #while i < iclaims_cnt:
   #     scores[bm25_vclaim_results.loc[index, 'vclaim_id']] = bm25_vclaim_results.loc[index, 'score']
   #     i = i + 1
    #    index = index + 1
    
    print(scores)
    scores = sorted(list(scores.items()), key=lambda kv: kv[1], reverse=True)
    print(iclaim_id, scores)
    all_scores[iclaim_id] = scores
    iclaim_index = iclaim_index + 1
    index = index - N + cnt_vclaims

{'vclaim-sno-single-mother-birth-certificate': 6.97253121, 'vclaim-sno-tennessee-bill-children-illegitimate': 1.31640143, 'vclaim-sno-birth-certificates-financial-accounts': 2.03723564, 'vclaim-sno-texas-birth-certificates-illegals': 2.13819059, 'vclaim-sno-barron-trump-benefit-birthright-citizenship': 0.41527229, 'vclaim-sno-colorado-birth-control-facts': 1.57914851, 'vclaim-sno-breastfeeding-size-ban': 0.75786876, 'vclaim-sno-james-maxwell-trump-son': 3.45746749, 'vclaim-sno-jeff-guice-sick-children': 0.28834882, 'vclaim-sno-oklahoma-bill-lgbt-adoptions': 0.27291413, 'vclaim-sno-hawaii-official-no-obama-birth-certificate': 1.68341976, 'vclaim-sno-rumor-alert-biden-michigan-votes': 0.24459463, 'vclaim-sno-john-kasich-said-we-cant-entrust-abortion-decision-to-women': 0.61402807, 'vclaim-sno-paul-ryans-wife-is-a-liberal-who-voted-twice-for-obama': 0.65027818, 'vclaim-sno-baby-boom-6': 1.83833074, 'vclaim-sno-u-s-senate-candidate-missouri-womans-rights': 0.77786594, 'vclaim-sno-birthing-

{'vclaim-sno-three-countries-issue-travel-warnings-about-the-united-states': 9.29540714, 'vclaim-sno-uk-issues-lgbt-travel-warning-for-united-states': 4.01036655, 'vclaim-sno-trump-visa-free-travel-policy': 2.5444446, 'vclaim-sno-aclu-travel-warning-texas': 4.55157206, 'vclaim-sno-african-union-issues-travel-advisory-for-u-s': 2.10276802, 'vclaim-sno-atheist-iceland-issues-travel-ban-white-southern-baptists': 2.96142048, 'vclaim-sno-cdc-ted-cruz-mexico': 2.60229322, 'vclaim-sno-sweden-sign-distracted-walkers': 1.81341405, 'vclaim-sno-highway-sign-consider-canada': 0.27702379, 'vclaim-sno-jehovahs-witness-russia-trump-asylum': 1.04362111, 'vclaim-sno-maximum-capacity-bridge-americans': 2.10085715, 'vclaim-sno-karolyi-illegal-immigrants': 1.2151588, 'vclaim-sno-trumps-muslim-ban-exclude-countries-businesses': 2.59293642, 'vclaim-sno-biometric-passports': 1.36871396, 'vclaim-sno-usps-mailboxes-removed-oregon': 1.04929935, 'vclaim-sno-terrorist-attacks-entry-restriction': 1.55748528, 'vcla

In [28]:
print(all_scores)

{'tweet-sno-999': [('vclaim-sno-single-mother-birth-certificate', 6.97253121), ('vclaim-sno-james-maxwell-trump-son', 3.45746749), ('vclaim-sno-texas-birth-certificates-illegals', 2.13819059), ('vclaim-sno-birth-certificates-financial-accounts', 2.03723564), ('vclaim-sno-marco-rubio-on-zika-and-abortion', 1.98781487), ('vclaim-sno-woman-buried-alive-twins', 1.92247365), ('vclaim-sno-baby-boom-6', 1.83833074), ('vclaim-sno-birth-certificate', 1.79273443), ('vclaim-sno-hawaii-official-no-obama-birth-certificate', 1.68341976), ('vclaim-sno-colorado-birth-control-facts', 1.57914851), ('vclaim-sno-after-birth-abortion', 1.55444116), ('vclaim-sno-gender-neutral-birth-certificates', 1.53119299), ('vclaim-sno-paul-ryan-birth-control-murder', 1.50218553), ('vclaim-sno-child-abduction-kansas', 1.47773517), ('vclaim-sno-paper-chase', 1.44217144), ('vclaim-sno-birthing-pains', 1.42127178), ('vclaim-sno-the-old-college-sigh', 1.39521772), ('vclaim-sno-oklahoma-host-woman-humphrey', 1.36571096), ('v

In [29]:
def format_scores(scores):
    output_string = ''
    i = 1
    for iclaim_id in scores:
        i = i + 1
        for i, (vclaim_id, score) in enumerate(scores[iclaim_id]):
            output_string += f"{iclaim_id}\tQ0\t{vclaim_id}\t{i + 1}\t{score}\tDIPS\n"
    return output_string

In [30]:
formatted_scores = format_scores(all_scores)
rank_svm_file = 'rank_top' + str(N) + '_dev_sbert.tsv'
with open(rank_svm_file, 'w') as f:
    f.write(formatted_scores)

In [31]:
from scorer.main import evaluate
import logging

maps, mrr, precisions = evaluate(dev_file_path, rank_svm_file)
logging.info(f'All MAP scores on threshold from [1, 3, 5, 10, 20, 50, 1000]. {maps}')
logging.info(f'MRR score {mrr}')
logging.info(f'All P scores on threshold from [1, 3, 5, 10, 20, 50, 1000]. {precisions}')

INFO : All MAP scores on threshold from [1, 3, 5, 10, 20, 50, 1000]. [0.907035175879397, 0.9212730318257957, 0.9235343383584591, 0.9252093802345059, 0.9260146888287593, 0.9262539805253373, 0.9262539805253373]
INFO : MRR score 0.9237414177112669
INFO : All P scores on threshold from [1, 3, 5, 10, 20, 50, 1000]. [0.9045226130653267, 0.3132328308207705, 0.18994974874371853, 0.0959798994974874, 0.04849246231155778, 0.01949748743718593, 0.0009748743718592968]
